In [17]:
import torch
from transformers import (
    RobertaTokenizerFast,
    RobertaForSequenceClassification,
    TrainingArguments,
    Trainer,
    AutoConfig,
)


In [18]:
from sklearn.model_selection import train_test_split
import pandas as pd
from sklearn.model_selection import train_test_split


# Load your preprocessed dataset into a pandas DataFrame
df = pd.read_csv(r'D:\Thesis\Datasets\preprocessed_dataset.csv')
df = df.dropna()
df.head()

#independent variable
X = list(df['sentence'])
#dependent variable
y = list(df['label'])

#splitting
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size= 0.20, random_state= 0)

In [19]:
tokenizer = RobertaTokenizerFast.from_pretrained("jcblaise/roberta-tagalog-base")
def tokenize(batch):
    return tokenizer(batch["text"], padding=True, truncation=True, max_length=97)

In [20]:
# Calculate the length of each input sequence
sequence_lengths = [len(tokenizer.tokenize(text)) for text in X_train]

# Print statistics about sequence lengths
print("Maximum sequence length:", max(sequence_lengths))
print("Minimum sequence length:", min(sequence_lengths))
print("Average sequence length:", sum(sequence_lengths) / len(sequence_lengths))


Maximum sequence length: 146
Minimum sequence length: 5
Average sequence length: 34.3118799903218


In [21]:
from datasets import Dataset

# Create datasets using the Dataset class
train_dataset = Dataset.from_dict({"text": X_train, "label": y_train})
val_dataset = Dataset.from_dict({"text": X_test, "label": y_test})

# Tokenize datasets using the tokenize function
train_dataset = train_dataset.map(tokenize, batched=True)
val_dataset = val_dataset.map(tokenize, batched=True)





Map: 100%|██████████| 8266/8266 [00:00<00:00, 14158.16 examples/s]


Map: 100%|██████████| 2067/2067 [00:00<00:00, 15252.23 examples/s]


In [22]:
# Define your model configuration
model_config = RobertaForSequenceClassification.from_pretrained("jcblaise/roberta-tagalog-base")

# Define your training arguments
training_args = TrainingArguments(
    output_dir='./results',
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    logging_dir='./logs',
    logging_steps=100,
    evaluation_strategy="steps",
    eval_steps=500,
)

# Initialize Trainer
trainer = Trainer(
    model=model_config,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset
)


Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at jcblaise/roberta-tagalog-base and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [23]:
trainer.train()

  0%|          | 0/3102 [02:45<?, ?it/s]
                                                    
  3%|▎         | 100/3102 [03:56<2:00:25,  2.41s/it]

{'loss': 0.6868, 'learning_rate': 4.8388136686009026e-05, 'epoch': 0.1}


                                                    
  6%|▋         | 200/3102 [07:51<1:49:08,  2.26s/it]

{'loss': 0.5552, 'learning_rate': 4.677627337201805e-05, 'epoch': 0.19}


                                                    
 10%|▉         | 300/3102 [11:40<2:00:36,  2.58s/it]

...

                                                       
100%|█████████▉| 3100/3102 [2:05:16<00:04,  2.09s/it]

{'loss': 0.182, 'learning_rate': 3.2237266279819476e-08, 'epoch': 3.0}


                                                     
100%|██████████| 3102/3102 [2:05:19<00:00,  2.42s/it]

{'train_runtime': 7519.6848, 'train_samples_per_second': 3.298, 'train_steps_per_second': 0.413, 'train_loss': 0.3369909449403014, 'epoch': 3.0}


TrainOutput(global_step=3102, training_loss=0.3369909449403014, metrics={'train_runtime': 7519.6848, 'train_samples_per_second': 3.298, 'train_steps_per_second': 0.413, 'train_loss': 0.3369909449403014, 'epoch': 3.0})

In [24]:
# Evaluate the model
results = trainer.evaluate()

# Print evaluation results
print(results)

100%|██████████| 259/259 [02:31<00:00,  1.71it/s]

{'eval_loss': 0.7732343077659607, 'eval_runtime': 152.402, 'eval_samples_per_second': 13.563, 'eval_steps_per_second': 1.699, 'epoch': 3.0}


In [25]:
# Save the fine-tuned model
trainer.save_model("./fine_tuned_model")

# Save the tokenizer
tokenizer.save_pretrained("./fine_tuned_model")


('./fine_tuned_model\\tokenizer_config.json',
 './fine_tuned_model\\special_tokens_map.json',
 './fine_tuned_model\\vocab.json',
 './fine_tuned_model\\merges.txt',
 './fine_tuned_model\\added_tokens.json',
 './fine_tuned_model\\tokenizer.json')

In [26]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Evaluate the model
predictions = trainer.predict(val_dataset)
predicted_labels = predictions.predictions.argmax(-1)
true_labels = val_dataset['label']

# Compute evaluation metrics
accuracy = accuracy_score(true_labels, predicted_labels)
precision = precision_score(true_labels, predicted_labels, average='weighted')
recall = recall_score(true_labels, predicted_labels, average='weighted')
f1 = f1_score(true_labels, predicted_labels, average='weighted')

accuracy_percentage = accuracy * 100
precision_percentage = precision * 100
recall_percentage = recall * 100
f1_percentage = f1 * 100

print("Accuracy:", accuracy_percentage)
print("Precision:", precision_percentage)
print("Recall:", recall_percentage)
print("F1-score:", f1_percentage)

100%|██████████| 259/259 [02:32<00:00,  1.70it/s]

Accuracy: 81.8577648766328
Precision: 82.02415819804327
Recall: 81.8577648766328
F1-score: 81.84955953514542


In [29]:
import torch
from transformers import RobertaTokenizerFast, RobertaForSequenceClassification

# Load the fine-tuned model and tokenizer
model_path = "./fine_tuned_model"
tokenizer = RobertaTokenizerFast.from_pretrained(model_path)
model = RobertaForSequenceClassification.from_pretrained(model_path)

# Set the model to evaluation mode
model.eval()

# Sample sentence for testing
sample_sentence = "Takbo sya nang takbo kanina kaya sya nadapa"

# Tokenize the input sentence
inputs = tokenizer(sample_sentence, return_tensors="pt")

# Forward pass through the model
with torch.no_grad():
    outputs = model(**inputs)

# Get the predicted class (label) from the model output
predicted_class = torch.argmax(outputs.logits).item()

print("Accuracy:", accuracy_percentage)
print("Precision:", precision_percentage)
print("Recall:", recall_percentage)
print("F1-score:", f1_percentage)
print("----------------------------")

if predicted_class == 1:
    print("Sentence is grammatically correct.")
else:
    print("Sentence is grammatically wrong.")



Accuracy: 81.8577648766328
Precision: 82.02415819804327
Recall: 81.8577648766328
F1-score: 81.84955953514542
----------------------------
Sentence is grammatically correct.
